- This notebook performs density based clustering of transcripts into nuclear, somatic and extra-somatic 

1. Load the expression matrix

In [ ]:
import scanpy as sc
fl = r'./../../20250626_hBG_2724_GPie/annotated_anndata/2724_Gpe_Gpi_leiden_clustered_mapmycellAnnotated.h5ad'
scdata2 = sc.read_h5ad(fl)

2. Get the decoded transcript files 

In [ ]:
import glob,os
fls = glob.glob(r'./../../Raw_custom_MERFISH_Imaging_data/20250626_hBG_2724_GPie/HumanBG_MERFISH_Filtered_Spots/Conv_zscan__*--spots.npz')

3. Run the density based clustering 

In [ ]:
for e1 in np.unique(scdata2.obs['Group_name']):
    
    #e1 = 'VIP GABA'
    mn_all = np.mean(scdata2[:,gns].X,axis=0)
    meanDH = np.mean(scdata2[:,gns][scdata2.obs['Group_name']==e1].X,axis=0)-mn_all
    N=20
    plt.figure()
    plt.plot(np.sort(meanDH)[::-1][:N],'o-')
    plt.xticks(np.arange(N),gns[np.argsort(meanDH)][::-1][:N],rotation='vertical');
    plt.title(e1)
    
    iindex = np.where(scdata2.obs['Group_name']==e1)[0]
    best_cor = np.argsort([np.corrcoef(meanDH,e)[0,1]for e in scdata2.X[iindex]-mn_all])[::-1]
    ibest_cells = scdata2.obs.index[iindex[best_cor]]
    
    volms = []
    for icellSEL in np.arange(100):
        try:
            ibest = ibest_cells[icellSEL]#30
            fov,cell = ibest.split('--')
            fl_load = [fl_ for fl_ in fls if fov in fl_][0]
            
            header = list(np.load(fl_load)['header'])
            icell_id = header.index('cell_id')
            XF = np.load(fl_load)['XF']
            icell = XF[:,icell_id]
            genes = np.load(fl_load)['genes']
            
            gns_,cts_ = np.unique(genes[icell==int(cell)],return_counts=True)
            dic_cts = dict(zip(gns_,cts_/np.sum(cts_)))
            gns_,cts_ = np.unique(genes[icell==0],return_counts=True)
            dic_cts_bk = dict(zip(gns_,cts_/np.sum(cts_)))
            enrich = np.array([dic_cts[gn]/dic_cts_bk.get(gn,0)for gn in dic_cts])
            gns_kp = np.array(list(dic_cts.keys()))[enrich>3]
            gns_kp = np.intersect1d(gns_kp,gns[meanDH>0])
            kp = np.in1d(genes,gns_kp)#,gns[meanDH>0.4])
            
            if False:
                import napari
                VV = napari.Viewer()#napari.view_points(XF[:,1:3],size=1,edge_width=0)#[genes=='CHAT'])
                kp = np.in1d(genes,gns_kp)#,gns[meanDH>0.4])
                #kp = np.in1d(genes,)
                VV.add_points(XF[kp,:3]*[0.5,0.10833,0.10833],size=1,face_color='g',edge_width=0)#[genes=='CHAT'])
                VV.add_points(XF[icell==int(cell),:3]*[0.5,0.10833,0.10833],size=1)
            
            Xall = XF[:,:3]*[0.5,0.10833,0.10833]
            Xall_kp = Xall[kp]
            X_cell_kp = Xall[(icell==int(cell))&kp]
            from scipy.spatial import KDTree
            N=5
            dd,ii=KDTree(X_cell_kp).query(X_cell_kp,N)
            dth = np.median(dd[:,-1])
            X_bk = Xall[(icell==0)&kp]
            dd,ii=KDTree(X_bk).query(X_bk,N)
            dth_bk = np.median(dd[:,-1])
            from sklearn.cluster import DBSCAN
            dbscan = DBSCAN(eps=(dth+dth_bk)/2,min_samples=N)
            lab = dbscan.fit(Xall_kp).labels_
            
            ulab = np.unique(lab)
            mean_cell = [np.mean(icell[kp][lab==ilab]==int(cell)) for ilab in ulab]
            best = ulab[np.argmax(mean_cell)]
            dd,ii = KDTree(Xall_kp).query(X_cell_kp)
            bd,cts = np.unique(lab[ii],return_counts=True)
            best=bd[np.argmax(cts)]
            
            
            if False:
                VV = napari.Viewer(ndisplay=3)#napari.view_points(XF[:,1:3],size=1,edge_width=0)#[genes=='CHAT'])
                kp = np.in1d(genes,gns_kp)#,gns[meanDH>0.4])
                #kp = np.in1d(genes,)
                VV.add_points(XF[kp,:3]*[0.5,0.10833,0.10833],size=1,face_color='r',edge_width=0,shading='spherical')#[genes=='CHAT'])
                #VV.add_points(XF[icell==int(cell),:3]*[0.5,0.10833,0.10833],size=1,shading='spherical')
                VV.add_points(Xall_kp[best==lab],size=1.25,face_color='g',shading='spherical',edge_width=0)
                VV.camera.zoom=8.5
                VV.camera.center=np.mean(Xall_kp[best==lab],axis=0)
                VV.screenshot(rf'./../../Raw_custom_MERFISH_Imaging_data/20250626_hBG_2724_GPie/NeuronImages/{e1}_icell{icellSEL}_dots.png')
                VV.close()
            
            X = Xall_kp[best==lab]
            if False:
                res = 10
                Xint = np.round(X*res).astype(int)
                #Xint = Xint-np.min(Xint,axis=0)+res*2
                #sz = np.max(Xint,axis=0)+res*4
                sz = np.array([200,750,750])
                Xint = (Xint-np.mean(Xint,axis=0)+sz/2).astype(int)
                Xint = Xint[np.all((Xint>0)&(Xint<sz),axis=-1)]
                im = np.zeros(sz)
                im[tuple(Xint.T)]+=1
                #napari.view_image(im)
                from scipy import ndimage
                img = ndimage.gaussian_filter(im,res/1.)>0.0001
                VV = napari.Viewer(ndisplay=3)
                VV.add_image(img)
                layer = VV.layers[0]
                layer.rendering='iso'
                layer.iso_threshold=0
                VV.camera.zoom = 0.75
                VV.screenshot(rf'./../../Raw_custom_MERFISH_Imaging_data/20250626_hBG_2724_GPie/NeuronImages/{e1}_icell{icellSEL}_volm.png')
                VV.close()
                volm = (np.sum(img)*0.001)
                volms.append(volm)
        
            segm_fl = fl_load.replace('HumanBG_MERFISH_Filtered_Spots','Segmentation').replace('--spots','--H1_MER_set1--dapi_segm')
            segm = np.load(segm_fl)['segm']
            shape = np.load(segm_fl)['shape']
            from scipy import ndimage
            imsegmf = ndimage.binary_erosion(segm==int(cell),iterations=3)
            Xnuc = np.array(np.where(imsegmf)).T*shape/segm.shape*[0.5,0.10833,0.10833]
            dd,ii = KDTree(X).query(XF[:,:3]*[0.5,0.10833,0.10833])
            kpf = dd<2
            XF_all = XF[kpf,:]
            genes_all = genes[kpf]
        
            dd,ii = KDTree(X).query(Xall_kp)
            Xneigh = Xall_kp[dd<20]
            dd,ii = KDTree(Xneigh).query(XF[:,:3]*[0.5,0.10833,0.10833])
            Xneigh = Xneigh[ii[dd==0]]
            genes_neigh = genes[dd==0]
            np.savez_compressed(rf'./../../Raw_custom_MERFISH_Imaging_data/20250626_hBG_2724_GPie/NeuronImagesV2/{e1}_icell{icellSEL}_info.npz',X=X,Xnuc=Xnuc,Xnuc0=Xnuc0,XF_all=XF_all,genes_all=genes_all,pix_size= [0.5,0.10833,0.10833],Xneigh=Xneigh,genes_neigh=genes_neigh)
        
            V=napari.Viewer(ndisplay=3)
            V.add_points(X,blending='Additive',face_color='g',size=1,edge_width=0,shading='spherical')
            V.add_points(Xneigh,blending='Additive',face_color='r',size=1,edge_width=0,shading='spherical')
            V.add_points(Xnuc,blending='Additive',face_color='b',size=1,edge_width=0)
            V.scale_bar.visible = True
            V.scale_bar.length = 10
            V.reset_view()
            V.screenshot(rf'./../../Raw_custom_MERFISH_Imaging_data/20250626_hBG_2724_GPie/NeuronImagesV2/{e1}_icell{icellSEL}_dots.png')
            V.close()
        except:
            print("Failed")

C:\Users\exx\.conda\envs\MERFISH_postproc\Lib\site-packages\numpy\core\fromnumeric.py:3504: RuntimeWarning: Mean of empty slice.
  return _methods._mean(a, axis=axis, dtype=dtype,
C:\Users\exx\.conda\envs\MERFISH_postproc\Lib\site-packages\numpy\core\_methods.py:129: RuntimeWarning: invalid value encountered in scalar divide
  ret = ret.dtype.type(ret / rcount)


Failed
Failed
Failed
Failed
Failed


C:\Users\exx\AppData\Local\Temp\ipykernel_34868\2936968348.py:124: FutureWarning: Argument 'edge_width' is deprecated, please use 'border_width' instead. The argument 'edge_width' was deprecated in 0.5.0 and it will be removed in 0.6.0.
  V.add_points(X,blending='Additive',face_color='g',size=1,edge_width=0,shading='spherical')
C:\Users\exx\AppData\Local\Temp\ipykernel_34868\2936968348.py:125: FutureWarning: Argument 'edge_width' is deprecated, please use 'border_width' instead. The argument 'edge_width' was deprecated in 0.5.0 and it will be removed in 0.6.0.
  V.add_points(Xneigh,blending='Additive',face_color='r',size=1,edge_width=0,shading='spherical')
C:\Users\exx\AppData\Local\Temp\ipykernel_34868\2936968348.py:126: FutureWarning: Argument 'edge_width' is deprecated, please use 'border_width' instead. The argument 'edge_width' was deprecated in 0.5.0 and it will be removed in 0.6.0.
  V.add_points(Xnuc,blending='Additive',face_color='b',size=1,edge_width=0)
C:\Users\exx\.conda\en

Failed
Failed
Failed
Failed
Failed
Failed
Failed
Failed
Failed
Failed


C:\Users\exx\AppData\Local\Temp\ipykernel_34868\2936968348.py:33: RuntimeWarning: divide by zero encountered in scalar divide
  enrich = np.array([dic_cts[gn]/dic_cts_bk.get(gn,0)for gn in dic_cts])


...

C:\Users\exx\AppData\Local\Temp\ipykernel_34868\2936968348.py:124: FutureWarning: Argument 'edge_width' is deprecated, please use 'border_width' instead. The argument 'edge_width' was deprecated in 0.5.0 and it will be removed in 0.6.0.
  V.add_points(X,blending='Additive',face_color='g',size=1,edge_width=0,shading='spherical')
C:\Users\exx\AppData\Local\Temp\ipykernel_34868\2936968348.py:125: FutureWarning: Argument 'edge_width' is deprecated, please use 'border_width' instead. The argument 'edge_width' was deprecated in 0.5.0 and it will be removed in 0.6.0.
  V.add_points(Xneigh,blending='Additive',face_color='r',size=1,edge_width=0,shading='spherical')
C:\Users\exx\AppData\Local\Temp\ipykernel_34868\2936968348.py:126: FutureWarning: Argument 'edge_width' is deprecated, please use 'border_width' instead. The argument 'edge_width' was deprecated in 0.5.0 and it will be removed in 0.6.0.
  V.add_points(Xnuc,blending='Additive',face_color='b',size=1,edge_width=0)
C:\Users\exx\AppData\L

Failed


C:\Users\exx\AppData\Local\Temp\ipykernel_34868\2936968348.py:124: FutureWarning: Argument 'edge_width' is deprecated, please use 'border_width' instead. The argument 'edge_width' was deprecated in 0.5.0 and it will be removed in 0.6.0.
  V.add_points(X,blending='Additive',face_color='g',size=1,edge_width=0,shading='spherical')
C:\Users\exx\AppData\Local\Temp\ipykernel_34868\2936968348.py:125: FutureWarning: Argument 'edge_width' is deprecated, please use 'border_width' instead. The argument 'edge_width' was deprecated in 0.5.0 and it will be removed in 0.6.0.
  V.add_points(Xneigh,blending='Additive',face_color='r',size=1,edge_width=0,shading='spherical')
C:\Users\exx\AppData\Local\Temp\ipykernel_34868\2936968348.py:126: FutureWarning: Argument 'edge_width' is deprecated, please use 'border_width' instead. The argument 'edge_width' was deprecated in 0.5.0 and it will be removed in 0.6.0.
  V.add_points(Xnuc,blending='Additive',face_color='b',size=1,edge_width=0)
C:\Users\exx\AppData\L

Failed


C:\Users\exx\AppData\Local\Temp\ipykernel_34868\2936968348.py:33: RuntimeWarning: divide by zero encountered in scalar divide
  enrich = np.array([dic_cts[gn]/dic_cts_bk.get(gn,0)for gn in dic_cts])
C:\Users\exx\AppData\Local\Temp\ipykernel_34868\2936968348.py:124: FutureWarning: Argument 'edge_width' is deprecated, please use 'border_width' instead. The argument 'edge_width' was deprecated in 0.5.0 and it will be removed in 0.6.0.
  V.add_points(X,blending='Additive',face_color='g',size=1,edge_width=0,shading='spherical')
C:\Users\exx\AppData\Local\Temp\ipykernel_34868\2936968348.py:125: FutureWarning: Argument 'edge_width' is deprecated, please use 'border_width' instead. The argument 'edge_width' was deprecated in 0.5.0 and it will be removed in 0.6.0.
  V.add_points(Xneigh,blending='Additive',face_color='r',size=1,edge_width=0,shading='spherical')
C:\Users\exx\AppData\Local\Temp\ipykernel_34868\2936968348.py:126: FutureWarning: Argument 'edge_width' is deprecated, please use 'borde